In [2]:
import pandas as pd
import numpy as np
import smile_extract
import logging
logging.basicConfig(level=logging.DEBUG)

path = '/Users/raeed/Library/CloudStorage/OneDrive-UniversityofPittsburgh/0-projects/cst-rtt/cst-data/preTD/Dwight/2025-01-07/Dwight_2025-01-07_reward-type_medium_cst-rtt-dco_sorted.mat'
smile_data = smile_extract.direct_load_smile_data(path)

In [40]:
tf = smile_extract.compose_session_frame(smile_data)
tf

INFO:smile_extract.neural:Removing 0 of 138 units with average firing rate less than 0.1 Hz.
DEBUG:smile_extract.neural:Units removed:
 Series([], Name: average firing rate, dtype: float64)
INFO:smile_extract.neural:Removing 14 of 138 units with spike coincidence greater than 0.2.
DEBUG:smile_extract.neural:Units removed:
 MultiIndex([( 45, 1),
            ( 48, 1),
            ( 54, 1),
            ( 55, 1),
            ( 70, 1),
            ( 71, 1),
            ( 72, 1),
            (101, 1),
            (102, 1),
            (109, 1),
            (110, 1),
            (121, 1),
            (121, 2),
            (123, 1)],
           names=['channel', 'unit'])


channel                          monkey session date block  \
signal                                                       
trial_id time                                                
1        0 days 00:00:00         Dwight   2025-01-07         
         0 days 00:00:00.010000  Dwight   2025-01-07         
         0 days 00:00:00.020000  Dwight   2025-01-07         
         0 days 00:00:00.030000  Dwight   2025-01-07         
         0 days 00:00:00.040000  Dwight   2025-01-07         
...                                 ...          ...   ...   
152      0 days 00:00:04.340000  Dwight   2025-01-07         
         0 days 00:00:04.350000  Dwight   2025-01-07         
         0 days 00:00:04.360000  Dwight   2025-01-07         
         0 days 00:00:04.370000  Dwight   2025-01-07         
         0 days 00:00:04.380000  Dwight   2025-01-07         

channel                              trial datetime task   result  \
signal                                                              
trial_id time                                                       
1        0 days 00:00:00        2025-01-07 13:10:14  RTT  success   
         0 days 00:00:00.010000 2025-01-07 13:10:14  RTT  success   
         0 days 00:00:00.020000 2025-01-07 13:10:14  RTT  success   
         0 days 00:00:00.030000 2025-01-07 13:10:14  RTT  success   
         0 days 00:00:00.040000 2025-01-07 13:10:14  RTT  success   
...                                             ...  ...      ...   
152      0 days 00:00:04.340000 2025-01-07 13:20:42  CST  success   
         0 days 00:00:04.350000 2025-01-07 13:20:42  CST  success   
         0 days 00:00:04.360000 2025-01-07 13:20:42  CST  success   
         0 days 00:00:04.370000 2025-01-07 13:20:42  CST  success   
         0 days 00:00:04.380000 2025-01-07 13:20:42  CST  success   

channel                                    state hand position              \
signal                                                       x           y   
trial_id time                                                                
1        0 days 00:00:00         Reach to Center     61.511639  796.000308   
         0 days 00:00:00.010000  Reach to Center     61.523815  796.008314   
         0 days 00:00:00.020000  Reach to Center     61.523992  796.014579   
         0 days 00:00:00.030000  Reach to Center     61.528734  796.005679   
         0 days 00:00:00.040000  Reach to Center     61.521756  795.999943   
...                                          ...           ...         ...   
152      0 days 00:00:04.340000          Success    131.019076  899.375467   
         0 days 00:00:04.350000          Success    130.678476  899.449719   
         0 days 00:00:04.360000          Success    130.328765  899.540967   
         0 days 00:00:04.370000          Success    129.983302  899.620873   
         0 days 00:00:04.380000          Success    129.675428  899.682388   

channel                                     ... motor cortex                  \
signal                                   z  ...      ch122u1 ch122u2 ch122u3   
trial_id time                               ...                                
1        0 days 00:00:00         45.378573  ...            0       0       0   
         0 days 00:00:00.010000  45.383986  ...            0       0       0   
         0 days 00:00:00.020000  45.373014  ...            0       1       0   
         0 days 00:00:00.030000  45.383058  ...            0       0       0   
         0 days 00:00:00.040000  45.400846  ...            0       0       0   
...                                    ...  ...          ...     ...     ...   
152      0 days 00:00:04.340000  11.113030  ...            0       0       0   
         0 days 00:00:04.350000  11.031885  ...            0       0       0   
         0 days 00:00:04.360000  10.946598  ...            0       0       0   
         0 days 00:00:04.370000  10.865358  ...            0       1       0   
         0 days 00:00:04.380000

In [37]:
smile_extract.trial_info.get_trial_datetime_str(smile_data[0])

Timestamp('2025-01-07 13:10:14')

In [56]:
spike_times = smile_extract.get_smile_spike_times(smile_data)
recording_duration = (
    spike_times
    .groupby('trial_id')
    ['timestamp']
    .agg(np.ptp)
    .sum()
)
min_firing_rate = 10
average_firing_rate = (
    spike_times
    .groupby(['channel','unit'])
    ['timestamp']
    .agg('count')
    .apply(lambda x: x / recording_duration.total_seconds())
)
(
    spike_times
    .reset_index()
    .set_index(['channel','unit'])
    .loc[average_firing_rate > min_firing_rate]
    .reset_index()
    .set_index(['trial_id','snippet_id'])
)

Removing 49 of 138 units with average firing rate less than 10 Hz.


In [27]:
import seaborn as sns
import matplotlib.pyplot as plt

spike_times = smile_extract.get_smile_spike_times(smile_data)
binned_spikes = smile_extract.bin_spikes(spike_times, bin_size='1ms')

uncoincident = (
    spike_times
    .pipe(smile_extract.remove_correlated_units)
    .pipe(smile_extract.bin_spikes, bin_size='1ms')
)
fig,ax = plt.subplots(1,2,figsize=(10,5))
sns.heatmap(np.corrcoef(binned_spikes.T),ax=ax[0])
sns.heatmap(np.corrcoef(uncoincident.T),ax=ax[1])

<Axes: >

In [21]:
coincident_units

MultiIndex([( 45, 1),
            ( 48, 1),
            ( 54, 1),
            ( 55, 1),
            ( 70, 1),
            ( 71, 1),
            ( 72, 1),
            (101, 1),
            (102, 1),
            (109, 1),
            (110, 1),
            (121, 1),
            (121, 2),
            (123, 1)],
           names=['channel', 'unit'])

In [ ]:
import altair as alt

alt.data_transformers.enable(max_rows=10000)
raster = (
    alt.Chart(
        tf
        .loc[152,'motor cortex']
        .stack()
        .rename('spikes')
        .loc[lambda x: x > 0]
        .reset_index()
        .assign(time=lambda x: x['time'].dt.total_seconds())
    ).mark_tick().encode(
        x='time:Q',
        y=alt.Y('signal:N').axis(labels=False,ticks=False).title('Neuron'),
    )
    .configure_tick(
        bandSize=2,
        thickness=0.5,
        color='black',
    )
    .configure_axis(
        grid=False,
    )
    .properties(width=800, height=200)
)
tf.loc[1,'motor cortex'].stack().rename('spikes').loc[lambda x: x > 0]
raster

In [ ]:
from src.extract_smile_data import get_smile_meta

temp = get_smile_meta(smile_data)
temp.groupby(['task','result']).size()
temp

In [ ]:
from src.extract_smile_data import get_trial_events,concat_trial_func_results

events=concat_trial_func_results(get_trial_events, smile_data)
(
    get_trial_events(smile_data[0])
    .reset_index(level='event')
    .set_index('time')
    .resample('10ms')
    .ffill()
    .rename(columns={'event':'state'})
    .squeeze()
)

In [ ]:
from src.extract_smile_data import get_trial_spike_times,bin_spikes,concat_trial_func_results

spike_times = concat_trial_func_results(
    get_trial_spike_times,
    smile_data,
    keep_sorted_only=True,
)
bin_spikes(spike_times)
spike_times

In [ ]:
smile_data[20]['TrialData']['stateTransitions'].T

In [ ]:
pd.DataFrame(smile_data[20]['Parameters']['StateTable']).columns
#pd.DataFrame(smile_data[0]['Parameters']['StateTable'])['stateName']
smile_data[21]['Parameters']['StateTable'][3]['stateName']

In [ ]:
import numpy as np
import altair as alt
from src.extract_smile_data import get_trial_hand_data,concat_trial_func_results

hand_data = concat_trial_func_results(
    get_trial_hand_data,
    smile_data,
    final_sampling_rate=100,
)

def sig_chart(df, **kwargs):
    return (
        alt.Chart(
            df
            .loc[:'0.2s']
            .reset_index()
            .assign(time=lambda x: x['time'].dt.total_seconds())
        )
        .mark_line(
            point='transparent',
            **kwargs
        )
        .encode(
            x='time:Q',
            y=alt.Y('x:Q').scale(zero=False),
        )
    )

(
    # sig_chart(marker_pos_df, color='black')
    # +
    sig_chart(hand_data.loc[1], color='blue')
)

In [ ]:
1/pd.to_timedelta('10ms').total_seconds()

In [ ]:
hand_data

In [ ]:
from src.extract_smile_data import get_spike_waveforms
from sklearn.decomposition import PCA
import altair as alt

waveforms = get_spike_waveforms(smile_data)

channel_waveforms = (
    waveforms
    .groupby('channel')
    .get_group(96)
    .rename(columns=lambda x: str(x))
)

channel_waveform_pca = pd.DataFrame(
    PCA(n_components=2)
    .fit_transform(
        channel_waveforms
    ),
    columns=['PC1','PC2'],
    index=channel_waveforms.index,
)

channel_waveforms = channel_waveforms.assign(**channel_waveform_pca)

sampled_waveforms = (
    channel_waveforms
    .sample(n=500)
    .reset_index()
)

# alt.data_transformers.enable('json')
selection = alt.selection_interval()

scatter = (
    alt.Chart(sampled_waveforms)
    .mark_point()
    .encode(
        x='PC1:Q',
        y='PC2:Q',
        color=alt.condition(
            selection,
            'unit:N',
            alt.value('lightgray'),
        ),
    )
    .add_selection(
        selection
    )
)

waveforms = (
    alt.Chart(sampled_waveforms)
    .mark_line()
    .encode(
        x='frame:Q',
        y='amplitude:Q',
        color=alt.condition(
            selection,
            'unit:N',
            alt.value('lightgray'),
        ),
        detail='snippet_id:O',
    )
    .transform_fold(
        [str(i) for i in range(30)],
        as_=['snippet_frame','amplitude'],
    )
    .transform_calculate(
        frame='toNumber(datum.snippet_frame)',
    )
)
scatter | waveforms

In [ ]:
tf